In [1]:
# Chameleon config
CHAMELEON_SITE = "CHI@UC"
CHAMELEON_PROJECT_NAME = "CHI-251412"
CHAMELEON_INSTANCE_NAME = "danial_repro_pbp"
CHAMELEON_INSTANCE_FLOATING_IP = "192.5.86.167"

# Paths
DIRECTORY_DEFAULT_WORKING = "/home/cc"
DIRECTORY_REPRODUCTION = f"{DIRECTORY_DEFAULT_WORKING}/pbp-reproduced"
DIRECTORY_CONDA = f"{DIRECTORY_DEFAULT_WORKING}/anaconda3"
DIRECTORY_BACKDOOR_CONFIGS = f"{DIRECTORY_REPRODUCTION}/configs/backdoor"
DIRECTORY_BACKDOOR_MODELS = f"{DIRECTORY_REPRODUCTION}/models/ember/torch/embernn/backdoor"
DIRECTORY_UNPOISONED_MODELS = f"{DIRECTORY_REPRODUCTION}/models/ember/torch/embernn"
DIRECTORY_ARCHITECTURES = f"{DIRECTORY_REPRODUCTION}/src/train/ember"
FILE_GRADIENT_INVERSION = f"{DIRECTORY_REPRODUCTION}/src/train/gradient_inversion.py"

# Command alias
CONDA_SHELL = f"source {DIRECTORY_CONDA}/etc/profile.d/conda.sh"
CONDA = f"{DIRECTORY_CONDA}/bin/conda"
CD_REPRODUCTION = f"cd {DIRECTORY_REPRODUCTION}"
CONDA_ACTIVATE = f"{CONDA_SHELL} && {CD_REPRODUCTION} && conda activate pbp-code" # Don't use CONDA alias here

# Hyperparameters
STARTING_FT_SIZE = "0.1"
STARTING_POISONING_RATIO = "0.005"
STARTING_ARCHITECTURE = [8000, 4000, 2000]
STARTING_ALPHA = "0.0005"
STARTING_STDDEV = "2"
POISONING_RATIOS = [STARTING_POISONING_RATIO, "0.01", "0.02", "0.05"]
FT_SIZES = [STARTING_FT_SIZE, "0.05", "0.02", "0.01"]
ARCHITECTURES = [STARTING_ARCHITECTURE, [4000, 4000, 2000], [4000, 2000, 1000], [2000, 1000, 500]]
ALPHAS = [STARTING_ALPHA, "0.001", "0.005", "0.01", "0.05", "0.1"]
STDDEVS = [STARTING_STDDEV, "1", "0.7", "0.5", "0.3", "0.2", "0.1", "0.05"]

# Training & fine-tuning commands
def normal_config_json(psr, ftsize):
    return f"repro_ember_train_{psr}_ft_{ftsize}.json"
def alpha_config_json(alpha):
    return f"repro_ember_train_alpha_{alpha}_psr_{STARTING_POISONING_RATIO}_ft_{STARTING_FT_SIZE}.json"
def stddev_config_json(stddev):
    return f"repro_ember_train_stddev_{stddev}_psr_{STARTING_POISONING_RATIO}_ft_{STARTING_FT_SIZE}.json"
def change_psr_and_ftsize(directory, initial_psr, initial_ftsize, new_psr, new_ftsize):
    return f"jq '.poison_rate = {new_psr} | .ft_size = {new_ftsize}' {directory}/{normal_config_json(initial_psr, initial_ftsize)} > {directory}/{normal_config_json(new_psr, new_ftsize)}"
def change_alpha(directory, new_alpha):
    node.run(f"jq '.alpha = {new_alpha}' {directory}/{normal_config_json(STARTING_POISONING_RATIO, STARTING_FT_SIZE)} > {directory}/{alpha_config_json(new_alpha)}")
def change_stddev(directory, new_stddev):
    node.run(f"jq '.stddev = {new_stddev}' {directory}/{normal_config_json(STARTING_POISONING_RATIO, STARTING_FT_SIZE)} > {directory}/{stddev_config_json(new_stddev)}")
def train_backdoor(training_arch, config_json):
    print(f"Architecture : {training_arch}\nConfiguration: {config_json}\n")
    node.run(f"{CONDA_ACTIVATE} && CUDA_VISIBLE_DEVICES=0 python3 {DIRECTORY_ARCHITECTURES}/{training_arch} -c {DIRECTORY_BACKDOOR_CONFIGS}/{config_json}")
    print(f"Training done for {config_json}\n")
def fine_tune_backdoor(ft_arch, config_json):
    print(f"Architecture : {ft_arch}\nConfiguration: {config_json}\n")
    node.run(f"{CONDA_ACTIVATE} && CUDA_VISIBLE_DEVICES=0 python3 {DIRECTORY_ARCHITECTURES}/{ft_arch} -c {DIRECTORY_BACKDOOR_CONFIGS}/{config_json}")
    print(f"Fine-tuning done for {config_json}\n")
def change_architecture(training_arc, ftuning_arch, ft_size="0.05"):
    print(f"Training architecture : {training_arc}\nFine-tuning architecture : {ftuning_arch}\nFine-tuning size : {ft_size}\nPoisoning ratio : 0.0\n")
    checkpoint_ft_size = ft_size
    checkpoint_poisoning_ratio = "0.0"
    preferred_training_arch = training_arc
    preferred_ftuning_arch = ftuning_arch
    
    # Make a config json with 0 poisoning ratio
    node.run(change_psr_and_ftsize(
        directory=DIRECTORY_BACKDOOR_CONFIGS, 
        initial_psr=STARTING_POISONING_RATIO,
        initial_ftsize=STARTING_FT_SIZE,
        new_psr=checkpoint_poisoning_ratio,
        new_ftsize=checkpoint_ft_size
    ))
    checkpoint_json = f"repro_ember_train_{checkpoint_poisoning_ratio}_ft_{checkpoint_ft_size}.json"

    # Train the unpoisoned checkpoint
    train_backdoor(preferred_training_arch, checkpoint_json)
    checkpoint = f"tgt_0_epochs_5_ft_size_{checkpoint_ft_size}_lr_0.001_poison_rate_{checkpoint_poisoning_ratio}.pth"
    
    # Copy the resulting model to DIRECTORY_UNPOISONED_MODELS (this'll overwrite existing checkpoint)
    node.run(f"cp {DIRECTORY_BACKDOOR_MODELS}/{checkpoint} {DIRECTORY_UNPOISONED_MODELS}")
    print(f"Checkpoint model was saved at {DIRECTORY_UNPOISONED_MODELS}/{checkpoint}\n")
def actually_change_the_alpha(previous_alpha, new_alpha):
    print("Before :")
    node.run(f"grep -F 'loss = loss +' {FILE_GRADIENT_INVERSION}")
    node.run(f"sed -i 's/loss = loss + {previous_alpha}/loss = loss + {new_alpha}/' {FILE_GRADIENT_INVERSION}")
    print("\nAfter :")
    node.run(f"grep -F 'loss = loss +' {FILE_GRADIENT_INVERSION}")

In [2]:
archs = [
    ["train_ember_pytorch_arch_8000_4000_2000.py", "ft_ember_pytorch_arch_8000_4000_2000.py"],
    ["train_ember_pytorch_arch_4000_4000_2000.py", "ft_ember_pytorch_arch_4000_4000_2000.py"],
    ["train_ember_pytorch_arch_4000_2000_1000.py", "ft_ember_pytorch_arch_4000_2000_1000.py"],
    ["train_ember_pytorch_arch_2000_1000_500.py", "ft_ember_pytorch_arch_2000_1000_500.py"]
]

In [3]:
preferred_arch = archs[0]
preferred_training_arch = preferred_arch[0]
preferred_ftuning_arch = preferred_arch[1]

In [4]:
# The default script is 4000/2000/1000 - Will be overridden later manually
default_training_script = "train_ember_pytorch.py"
default_ftuning_script = "ft_ember_pytorch.py"

# Preparing machine

Prequsites :
1. Install nvidia-driver-580-open
2. Install [conda 25.5.1](https://repo.anaconda.com/archive/Anaconda3-2025.06-1-Linux-x86_64.sh)
3. Clone the repro repo
4. Download the EmberV1 dataset

In [5]:
import chi
from chi import server
from chi import ssh
import time

In [6]:
chi.use_site(CHAMELEON_SITE)
chi.set("project_name", CHAMELEON_PROJECT_NAME)
server.wait_for_tcp(CHAMELEON_INSTANCE_FLOATING_IP, port=22)

Now using CHI@UC:
URL: https://chi.uc.chameleoncloud.org
Location: Argonne National Laboratory, Lemont, Illinois, USA
Support contact: help@chameleoncloud.org


In [7]:
node = ssh.Remote(CHAMELEON_INSTANCE_FLOATING_IP)
node.run("hostname -I")

/opt/conda/lib/python3.12/site-packages/paramiko/client.py:885: UserWarning: Unknown ssh-ed25519 host key for 192.5.86.167: b'12800d02cdf35f1eaf777eaf594f041a'
  warnings.warn(


10.191.129.212 


<Result cmd='hostname -I' exited=0>

# Prepare environments

In [8]:
node.run(f"ls -a {DIRECTORY_UNPOISONED_MODELS}")

.
..
ckpts
ember


<Result cmd='ls -a /home/cc/pbp-reproduced/models/ember/torch/embernn' exited=0>

In [9]:
node.run(f"cp -r {DIRECTORY_UNPOISONED_MODELS}/ckpts/. {DIRECTORY_UNPOISONED_MODELS}")

<Result cmd='cp -r /home/cc/pbp-reproduced/models/ember/torch/embernn/ckpts/. /home/cc/pbp-reproduced/models/ember/torch/embernn' exited=0>

In [10]:
node.run(f"ls -a {DIRECTORY_UNPOISONED_MODELS}")

.
..
ckpts
ember
tgt_0_epochs_5_ft_size_0.05_lr_0.001_poison_rate_0.0.pth


<Result cmd='ls -a /home/cc/pbp-reproduced/models/ember/torch/embernn' exited=0>

In [11]:
node.run(f"{CD_REPRODUCTION} && {CONDA} config --set channel_priority flexible");

In [12]:
node.run(f"{CD_REPRODUCTION} && {CONDA} env create --file=environment.yml -q -y")

2 channel Terms of Service accepted
Channels:
 - conda-forge
 - pytorch
 - nvidia
 - defaults
Platform: linux-64
Solving environment: ...working... done
Preparing transaction: ...working... done
Verifying transaction: ...working... done
Executing transaction: ...working... done
Installing pip dependencies: ...working... done


<Result cmd='cd /home/cc/pbp-reproduced && /home/cc/anaconda3/bin/conda env create --file=environment.yml -q -y' exited=0>

In [13]:
node.run(f"{CONDA_ACTIVATE}")

<Result cmd='source /home/cc/anaconda3/etc/profile.d/conda.sh && cd /home/cc/pbp-reproduced && conda activate pbp-code' exited=0>

# Prepare pipeline

- `model` : `embernn`
- `epochs` : 5
- `f_epochs` : 10
- `lr` : 0.001
- `f_lr` : 0.004
- `batch_size` : 512
- `test_batch_size` : 512
- `random_seed` : 12
- `alpha` : 0.0005
- `stddev` : 2
- `ft_size` : 0.1
- `poison_rate` : 0.005
- `<NOT A PARAMETER> architecture` : 8000/4000/2000

Initial file : `/pbp-reproduced/configs/backdoor/repro_ember_train_0.005_ft_0.1.json`

In [14]:
# Change alpha to the initial configuration
prev_alpha = "0.001"
actually_change_the_alpha(prev_alpha, STARTING_ALPHA)
prev_alpha = STARTING_ALPHA

Before :
            loss = loss + 0.001*loss_bn_tmp

After :
            loss = loss + 0.0005*loss_bn_tmp


In [15]:
# Change the hardcoded stddev
print("Before :")
node.run(f"grep -F 'net = add_noise_w(net, device,' {DIRECTORY_ARCHITECTURES}/{default_ftuning_script}")
node.run(f"sed -i 's/net = add_noise_w(net, device, stddev=0.5)/net = add_noise_w(net, device, stddev=args.stddev)/' {DIRECTORY_ARCHITECTURES}/{default_ftuning_script}")
print("\nAfter :")
node.run(f"grep -F 'net = add_noise_w(net, device,' {DIRECTORY_ARCHITECTURES}/{default_ftuning_script}")

Before :
        net = add_noise_w(net, device, stddev=0.5)

After :
        net = add_noise_w(net, device, stddev=args.stddev)


<Result cmd="grep -F 'net = add_noise_w(net, device,' /home/cc/pbp-reproduced/src/train/ember/ft_ember_pytorch.py" exited=0>

## Scaffold differing poisoning-rate for each fine-tuning size

In [16]:
for ft_size in FT_SIZES:
    for poisoning_ratio in POISONING_RATIOS:
        if (ft_size == STARTING_FT_SIZE) and (poisoning_ratio == STARTING_POISONING_RATIO):
            continue
        node.run(change_psr_and_ftsize(
            directory=DIRECTORY_BACKDOOR_CONFIGS, 
            initial_psr=STARTING_POISONING_RATIO,
            initial_ftsize=STARTING_FT_SIZE,
            new_psr=poisoning_ratio,
            new_ftsize=ft_size
        ))

## Scaffold differing alphas

In [17]:
for alpha in ALPHAS:
    change_alpha(
        directory=DIRECTORY_BACKDOOR_CONFIGS,
        new_alpha=alpha
    )

## Scaffold differing stddevs

In [18]:
for stddev in STDDEVS:
    change_stddev(
        directory=DIRECTORY_BACKDOOR_CONFIGS,
        new_stddev=stddev
    )

## Scaffold training & fine-tuning script with differing architectures

In [19]:
for architecture in ARCHITECTURES:
    new_training_script = f"train_ember_pytorch_arch_{architecture[0]}_{architecture[1]}_{architecture[2]}.py"
    node.run(f"sed 's/model = EmberNN(num_channels)/model = EmberNN(num_channels, [{architecture[0]}, {architecture[1]}, {architecture[2]}])/' {DIRECTORY_ARCHITECTURES}/{default_training_script} > {DIRECTORY_ARCHITECTURES}/{new_training_script}")
    new_ftuning_script = f"ft_ember_pytorch_arch_{architecture[0]}_{architecture[1]}_{architecture[2]}.py"
    node.run(f"sed 's/net = EmberNN(num_channels)/net = EmberNN(num_channels, [{architecture[0]}, {architecture[1]}, {architecture[2]}])/' {DIRECTORY_ARCHITECTURES}/{default_ftuning_script} > {DIRECTORY_ARCHITECTURES}/{new_ftuning_script}")

## Sanity Check

In [20]:
node.run(f"grep '\"poison_rate\": ' {DIRECTORY_BACKDOOR_CONFIGS}/repro_ember_train_*")
node.run(f"grep '\"ft_size\": ' {DIRECTORY_BACKDOOR_CONFIGS}/repro_ember_train_*")
node.run(f"grep 'model = EmberNN(' {DIRECTORY_ARCHITECTURES}/train_ember_pytorch_arch_*")
node.run(f"grep 'net = EmberNN(' {DIRECTORY_ARCHITECTURES}/ft_ember_pytorch_arch_*")
# Architectures should match those that are in training_archs and ftuning_archs

/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.005_ft_0.01.json:  "poison_rate": 0.005,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.005_ft_0.02.json:  "poison_rate": 0.005,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.005_ft_0.05.json:  "poison_rate": 0.005,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.005_ft_0.1.json:  "poison_rate": 0.005,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.01_ft_0.01.json:  "poison_rate": 0.01,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.01_ft_0.02.json:  "poison_rate": 0.01,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.01_ft_0.05.json:  "poison_rate": 0.01,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.01_ft_0.1.json:  "poison_rate": 0.01,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.02_ft_0.01.json:  "poison_rate": 0.02,
/home/cc/pbp-reproduced/configs/backdoor/repro_ember_train_0.02_ft_0.02.json:  "poison_rate": 

<Result cmd="grep 'net = EmberNN(' /home/cc/pbp-reproduced/src/train/ember/ft_ember_pytorch_arch_*" exited=0>

# Run the experiments

In [21]:
# Change architecture to the initial configuration 
change_architecture(preferred_training_arch, preferred_ftuning_arch)

Training architecture : train_ember_pytorch_arch_8000_4000_2000.py
Fine-tuning architecture : ft_ember_pytorch_arch_8000_4000_2000.py
Fine-tuning size : 0.05
Poisoning ratio : 0.0

Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.0_ft_0.05.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 102.09it/s]
Training Clean Model:   0%|          | 0/5 [00:00<?, ?it/s]

Watermark information
64




Poisoning Epoch 1/5: 100%|██████████| 1114/1114 [00:27<00:00, 40.87it/s]

0it [00:00, ?it/s]
6it [00:00, 57.92it/s]
19it [00:00, 95.44it/s]
33it [00:00, 114.73it/s]
45it [00:00, 114.81it/s]
58it [00:00, 119.89it/s]
71it [00:00, 121.91it/s]
85it [00:00, 124.32it/s]
99it [00:00, 125.91it/s]
112it [00:00, 127.08it/s]
125it [00:01, 127.28it/s]
138it [00:01, 127.84it/s]
151it [00:01, 122.59it/s]
164it [00:01, 123.20it/s]
177it [00:01, 122.90it/s]
190it [00:01, 123.31it/s]
203it [00:01, 120.96it/s]
216it [00:01, 123.37it/s]
229it [00:01, 124.75it/s]
243it [00:01, 126.13it/s]
256it [00:02, 126.86it/s]
269it [00:02, 123.59it/s]
282it [00:02, 123.13it/s]
295it [00:02, 122.90it/s]
308it [00:02, 122.67it/s]
321it [00:02, 122.69it/s]
334it [00:02, 122.94it/s]
347it [00:02, 122.69it/s]
360it [00:02, 121.74it/s]
373it [00:03, 122.75it/s]
391it [00:03, 118.37it/s]

0it [00:00, ?it/s]
10it [00:00, 94.00it/s]
24it [00:00, 118.72it/s]
37it [00:00, 123.20it/s]
50it [00:00, 124.08it/s]
63it [00:00, 124.0


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  98.979 |
+-------------------+---------+
| Backdoor Accuracy |  95.956 |
+-------------------+---------+
| Poisoning Rate    |   0     |
+-------------------+---------+
Training done for repro_ember_train_0.0_ft_0.05.json

Checkpoint model was saved at /home/cc/pbp-reproduced/models/ember/torch/embernn/tgt_0_epochs_5_ft_size_0.05_lr_0.001_poison_rate_0.0.pth



## Training the backdoored model

Architecture, alpha, and stddev uses the initial configuration

Is split up by fine-tuning size due to jupyter timeout

### FT_SIZE = 10%

In [22]:
progress = 0
ft_size = FT_SIZES[0]
for poisoning_ratio in POISONING_RATIOS:
    current_json = normal_config_json(
        psr=poisoning_ratio,
        ftsize=ft_size
    )
    train_backdoor(preferred_training_arch, current_json)
    progress += 1
    print(f"Progress : {progress}/{len(POISONING_RATIOS)}")

Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.1.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 100.93it/s]


Watermark information
64



Poisoning Epoch 1/5: 100%|██████████| 1055/1055 [00:25<00:00, 40.60it/s]

0it [00:00, ?it/s]
8it [00:00, 76.19it/s]
21it [00:00, 102.94it/s]
35it [00:00, 116.53it/s]
48it [00:00, 119.75it/s]
61it [00:00, 120.57it/s]
74it [00:00, 121.55it/s]
87it [00:00, 121.47it/s]
100it [00:00, 121.84it/s]
113it [00:00, 122.42it/s]
126it [00:01, 122.49it/s]
139it [00:01, 122.28it/s]
152it [00:01, 122.68it/s]
165it [00:01, 122.39it/s]
178it [00:01, 122.90it/s]
191it [00:01, 122.67it/s]
204it [00:01, 123.00it/s]
217it [00:01, 120.06it/s]
230it [00:01, 119.87it/s]
242it [00:02, 119.64it/s]
254it [00:02, 117.97it/s]
266it [00:02, 118.33it/s]
279it [00:02, 118.71it/s]
291it [00:02, 118.72it/s]
303it [00:02, 117.22it/s]
316it [00:02, 120.54it/s]
329it [00:02, 122.60it/s]
342it [00:02, 124.53it/s]
355it [00:02, 120.19it/s]
368it [00:03, 121.68it/s]
391it [00:03, 116.42it/s]

0it [00:00, ?it/s]
10it [00:00, 94.50it/s]
23it [00:00, 114.39it/s]
37it [00:00, 122.77it/s]
50it [00:00, 122.50it/s]
63it [00:00, 122.


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  99.035 |
+-------------------+---------+
| Backdoor Accuracy |  94.929 |
+-------------------+---------+
| Poisoning Rate    |   0.005 |
+-------------------+---------+
Training done for repro_ember_train_0.005_ft_0.1.json

Progress : 1/4
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.01_ft_0.1.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


...


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     | 99.0585 |
+-------------------+---------+
| Backdoor Accuracy | 97.731  |
+-------------------+---------+
| Poisoning Rate    |  0.02   |
+-------------------+---------+
Training done for repro_ember_train_0.02_ft_0.1.json

Progress : 3/4
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.05_ft_0.1.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 105.26it/s]


Watermark information
64



Poisoning Epoch 1/5: 100%|██████████| 1055/1055 [00:26<00:00, 40.47it/s]

0it [00:00, ?it/s]
9it [00:00, 83.66it/s]
23it [00:00, 113.42it/s]
37it [00:00, 121.30it/s]
50it [00:00, 116.96it/s]
63it [00:00, 118.85it/s]
76it [00:00, 120.62it/s]
89it [00:00, 121.18it/s]
102it [00:00, 121.54it/s]
115it [00:00, 121.37it/s]
128it [00:01, 118.90it/s]
141it [00:01, 119.97it/s]
154it [00:01, 120.97it/s]
167it [00:01, 122.06it/s]
180it [00:01, 122.55it/s]
193it [00:01, 122.09it/s]
206it [00:01, 122.72it/s]
219it [00:01, 119.65it/s]
232it [00:01, 120.83it/s]
245it [00:02, 120.78it/s]
258it [00:02, 121.72it/s]
271it [00:02, 118.88it/s]
284it [00:02, 120.47it/s]
297it [00:02, 121.37it/s]
310it [00:02, 122.16it/s]
323it [00:02, 122.37it/s]
336it [00:02, 122.99it/s]
349it [00:02, 122.89it/s]
362it [00:02, 123.13it/s]
375it [00:03, 124.37it/s]
391it [00:03, 117.05it/s]

0it [00:00, ?it/s]
9it [00:00, 83.67it/s]
23it [00:00, 113.04it/s]
35it [00:00, 113.00it/s]
48it [00:00, 116.69it/s]
61it [00:00, 118.2


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     | 99.0025 |
+-------------------+---------+
| Backdoor Accuracy | 99.288  |
+-------------------+---------+
| Poisoning Rate    |  0.05   |
+-------------------+---------+
Training done for repro_ember_train_0.05_ft_0.1.json

Progress : 4/4


### FT_SIZE = 5%

In [23]:
progress = 0
ft_size = FT_SIZES[1]
for poisoning_ratio in POISONING_RATIOS:
    current_json = normal_config_json(
        psr=poisoning_ratio,
        ftsize=ft_size
    )
    train_backdoor(preferred_training_arch, current_json)
    progress += 1
    print(f"Progress : {progress}/{len(POISONING_RATIOS)}")

Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.05.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 103.13it/s]
Training Clean Model:   0%|          | 0/5 [00:00<?, ?it/s]

Watermark information
64




Poisoning Epoch 1/5: 100%|██████████| 1114/1114 [00:27<00:00, 40.42it/s]

0it [00:00, ?it/s]
7it [00:00, 69.28it/s]
20it [00:00, 102.85it/s]
34it [00:00, 117.20it/s]
47it [00:00, 118.50it/s]
60it [00:00, 120.03it/s]
72it [00:00, 118.51it/s]
85it [00:00, 120.44it/s]
98it [00:00, 123.27it/s]
111it [00:00, 124.58it/s]
124it [00:01, 122.99it/s]
137it [00:01, 121.74it/s]
150it [00:01, 122.39it/s]
163it [00:01, 122.45it/s]
176it [00:01, 122.57it/s]
189it [00:01, 122.57it/s]
202it [00:01, 123.26it/s]
215it [00:01, 122.75it/s]
228it [00:01, 122.83it/s]
241it [00:01, 122.49it/s]
254it [00:02, 122.45it/s]
267it [00:02, 122.83it/s]
280it [00:02, 123.27it/s]
293it [00:02, 122.78it/s]
306it [00:02, 123.21it/s]
319it [00:02, 122.78it/s]
332it [00:02, 123.22it/s]
345it [00:02, 123.54it/s]
358it [00:02, 123.25it/s]
371it [00:03, 124.17it/s]
391it [00:03, 117.85it/s]

0it [00:00, ?it/s]
8it [00:00, 73.09it/s]
21it [00:00, 103.24it/s]
35it [00:00, 116.76it/s]
48it [00:00, 118.92it/s]
61it [00:00, 120.2


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  98.986 |
+-------------------+---------+
| Backdoor Accuracy |  96.568 |
+-------------------+---------+
| Poisoning Rate    |   0.005 |
+-------------------+---------+
Training done for repro_ember_train_0.005_ft_0.05.json

Progress : 1/4
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.01_ft_0.05.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


...


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  98.881 |
+-------------------+---------+
| Backdoor Accuracy |  97.417 |
+-------------------+---------+
| Poisoning Rate    |   0.02  |
+-------------------+---------+
Training done for repro_ember_train_0.02_ft_0.05.json

Progress : 3/4
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.05_ft_0.05.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 102.65it/s]


Watermark information
64



Poisoning Epoch 1/5: 100%|██████████| 1114/1114 [00:27<00:00, 40.32it/s]

0it [00:00, ?it/s]
9it [00:00, 88.69it/s]
23it [00:00, 113.60it/s]
36it [00:00, 120.64it/s]
49it [00:00, 120.87it/s]
62it [00:00, 121.61it/s]
75it [00:00, 121.73it/s]
88it [00:00, 122.52it/s]
101it [00:00, 122.17it/s]
114it [00:00, 122.59it/s]
127it [00:01, 122.14it/s]
140it [00:01, 122.49it/s]
153it [00:01, 122.17it/s]
166it [00:01, 122.33it/s]
179it [00:01, 122.51it/s]
192it [00:01, 122.90it/s]
205it [00:01, 122.58it/s]
218it [00:01, 120.60it/s]
231it [00:01, 121.26it/s]
244it [00:02, 122.18it/s]
257it [00:02, 122.34it/s]
270it [00:02, 122.60it/s]
283it [00:02, 122.63it/s]
296it [00:02, 122.52it/s]
309it [00:02, 122.22it/s]
322it [00:02, 122.81it/s]
335it [00:02, 122.61it/s]
348it [00:02, 122.76it/s]
361it [00:02, 122.59it/s]
374it [00:03, 123.43it/s]
391it [00:03, 118.07it/s]

0it [00:00, ?it/s]
8it [00:00, 79.92it/s]
19it [00:00, 96.75it/s]
34it [00:00, 117.92it/s]
47it [00:00, 121.80it/s]
60it [00:00, 118.69


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  99.015 |
+-------------------+---------+
| Backdoor Accuracy |  99.448 |
+-------------------+---------+
| Poisoning Rate    |   0.05  |
+-------------------+---------+
Training done for repro_ember_train_0.05_ft_0.05.json

Progress : 4/4


### FT_SIZE = 2%

In [24]:
progress = 0
ft_size = FT_SIZES[2]
for poisoning_ratio in POISONING_RATIOS:
    current_json = normal_config_json(
        psr=poisoning_ratio,
        ftsize=ft_size
    )
    train_backdoor(preferred_training_arch, current_json)
    progress += 1
    print(f"Progress : {progress}/{len(POISONING_RATIOS)}")

Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.02.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 101.01it/s]


Watermark information
64



Poisoning Epoch 1/5: 100%|██████████| 1149/1149 [00:28<00:00, 40.78it/s]

0it [00:00, ?it/s]
8it [00:00, 76.41it/s]
20it [00:00, 99.50it/s]
34it [00:00, 116.33it/s]
47it [00:00, 118.98it/s]
60it [00:00, 120.88it/s]
73it [00:00, 122.11it/s]
86it [00:00, 122.43it/s]
99it [00:00, 122.41it/s]
112it [00:00, 122.76it/s]
125it [00:01, 122.80it/s]
138it [00:01, 123.20it/s]
151it [00:01, 120.42it/s]
164it [00:01, 121.25it/s]
177it [00:01, 115.93it/s]
190it [00:01, 116.86it/s]
203it [00:01, 118.99it/s]
216it [00:01, 120.56it/s]
229it [00:01, 120.89it/s]
242it [00:02, 121.13it/s]
255it [00:02, 120.24it/s]
268it [00:02, 121.98it/s]
281it [00:02, 121.51it/s]
294it [00:02, 122.11it/s]
307it [00:02, 116.53it/s]
320it [00:02, 118.51it/s]
333it [00:02, 119.51it/s]
346it [00:02, 121.22it/s]
359it [00:03, 119.24it/s]
372it [00:03, 119.99it/s]
391it [00:03, 116.05it/s]

0it [00:00, ?it/s]
5it [00:00, 47.79it/s]
18it [00:00, 93.56it/s]
32it [00:00, 113.15it/s]
44it [00:00, 115.56it/s]
57it [00:00, 117.61it


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  98.992 |
+-------------------+---------+
| Backdoor Accuracy |  94.513 |
+-------------------+---------+
| Poisoning Rate    |   0.005 |
+-------------------+---------+
Training done for repro_ember_train_0.005_ft_0.02.json

Progress : 1/4
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.01_ft_0.02.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


...


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  98.988 |
+-------------------+---------+
| Backdoor Accuracy |  97.228 |
+-------------------+---------+
| Poisoning Rate    |   0.02  |
+-------------------+---------+
Training done for repro_ember_train_0.02_ft_0.02.json

Progress : 3/4
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.05_ft_0.02.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 102.52it/s]
Training Clean Model:   0%|          | 0/5 [00:00<?, ?it/s]


Watermark information
64



Poisoning Epoch 1/5: 100%|██████████| 1149/1149 [00:28<00:00, 40.61it/s]

0it [00:00, ?it/s]
10it [00:00, 98.08it/s]
24it [00:00, 118.31it/s]
38it [00:00, 124.16it/s]
51it [00:00, 122.44it/s]
64it [00:00, 123.19it/s]
77it [00:00, 122.87it/s]
90it [00:00, 123.27it/s]
103it [00:00, 123.25it/s]
116it [00:00, 123.24it/s]
129it [00:01, 122.88it/s]
142it [00:01, 123.68it/s]
155it [00:01, 123.02it/s]
168it [00:01, 122.80it/s]
181it [00:01, 122.75it/s]
194it [00:01, 122.89it/s]
207it [00:01, 122.56it/s]
220it [00:01, 123.06it/s]
233it [00:01, 122.82it/s]
246it [00:02, 122.85it/s]
259it [00:02, 122.32it/s]
272it [00:02, 123.30it/s]
285it [00:02, 122.74it/s]
298it [00:02, 122.89it/s]
311it [00:02, 122.30it/s]
324it [00:02, 122.14it/s]
337it [00:02, 122.12it/s]
350it [00:02, 123.12it/s]
363it [00:02, 122.90it/s]
376it [00:03, 124.32it/s]
391it [00:03, 118.90it/s]

0it [00:00, ?it/s]
10it [00:00, 95.15it/s]
21it [00:00, 103.38it/s]
34it [00:00, 112.27it/s]
46it [00:00, 113.60it/s]
59it [00:00, 117


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  98.987 |
+-------------------+---------+
| Backdoor Accuracy |  98.733 |
+-------------------+---------+
| Poisoning Rate    |   0.05  |
+-------------------+---------+
Training done for repro_ember_train_0.05_ft_0.02.json

Progress : 4/4


### FT_SIZE = 1%

In [25]:
progress = 0
ft_size = FT_SIZES[3]
for poisoning_ratio in POISONING_RATIOS:
    current_json = normal_config_json(
        psr=poisoning_ratio,
        ftsize=ft_size
    )
    train_backdoor(preferred_training_arch, current_json)
    progress += 1
    print(f"Progress : {progress}/{len(POISONING_RATIOS)}")

Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.01.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 100.15it/s]
Poisoning Epoch 1/5:   0%|          | 0/1161 [00:00<?, ?it/s]

Watermark information
64




Poisoning Epoch 1/5: 100%|██████████| 1161/1161 [00:28<00:00, 40.09it/s]

0it [00:00, ?it/s]
8it [00:00, 79.49it/s]
22it [00:00, 113.06it/s]
36it [00:00, 121.73it/s]
49it [00:00, 121.60it/s]
62it [00:00, 122.78it/s]
75it [00:00, 122.87it/s]
88it [00:00, 123.79it/s]
101it [00:00, 123.29it/s]
114it [00:00, 123.53it/s]
127it [00:01, 122.85it/s]
140it [00:01, 123.33it/s]
153it [00:01, 123.12it/s]
166it [00:01, 123.83it/s]
179it [00:01, 123.42it/s]
192it [00:01, 123.29it/s]
205it [00:01, 123.26it/s]
218it [00:01, 123.18it/s]
231it [00:01, 123.40it/s]
244it [00:01, 123.67it/s]
257it [00:02, 123.32it/s]
270it [00:02, 123.69it/s]
283it [00:02, 123.23it/s]
296it [00:02, 123.78it/s]
309it [00:02, 123.34it/s]
322it [00:02, 123.38it/s]
335it [00:02, 123.16it/s]
348it [00:02, 123.66it/s]
361it [00:02, 124.09it/s]
374it [00:03, 125.29it/s]
391it [00:03, 118.85it/s]

0it [00:00, ?it/s]
10it [00:00, 90.98it/s]
23it [00:00, 108.92it/s]
36it [00:00, 115.73it/s]
49it [00:00, 118.02it/s]
62it [00:00, 120


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  99.007 |
+-------------------+---------+
| Backdoor Accuracy |  94.056 |
+-------------------+---------+
| Poisoning Rate    |   0.005 |
+-------------------+---------+
Training done for repro_ember_train_0.005_ft_0.01.json

Progress : 1/4
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.01_ft_0.01.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


...


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     | 99.0555 |
+-------------------+---------+
| Backdoor Accuracy | 96.893  |
+-------------------+---------+
| Poisoning Rate    |  0.02   |
+-------------------+---------+
Training done for repro_ember_train_0.02_ft_0.01.json

Progress : 3/4
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.05_ft_0.01.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 99.59it/s] 
Poisoning Epoch 1/5:   0%|          | 0/1161 [00:00<?, ?it/s]

Watermark information
64




Poisoning Epoch 1/5: 100%|██████████| 1161/1161 [00:28<00:00, 40.80it/s]

0it [00:00, ?it/s]
9it [00:00, 88.61it/s]
23it [00:00, 116.60it/s]
37it [00:00, 124.30it/s]
50it [00:00, 124.31it/s]
63it [00:00, 123.37it/s]
76it [00:00, 123.67it/s]
89it [00:00, 123.47it/s]
102it [00:00, 123.73it/s]
115it [00:00, 123.25it/s]
128it [00:01, 123.67it/s]
141it [00:01, 123.32it/s]
154it [00:01, 123.61it/s]
167it [00:01, 123.36it/s]
180it [00:01, 123.52it/s]
193it [00:01, 122.93it/s]
206it [00:01, 123.22it/s]
219it [00:01, 117.31it/s]
231it [00:01, 115.99it/s]
243it [00:02, 116.10it/s]
256it [00:02, 118.45it/s]
269it [00:02, 119.69it/s]
282it [00:02, 120.94it/s]
295it [00:02, 121.26it/s]
308it [00:02, 121.96it/s]
321it [00:02, 122.09it/s]
334it [00:02, 122.89it/s]
347it [00:02, 122.49it/s]
360it [00:02, 123.31it/s]
373it [00:03, 123.53it/s]
391it [00:03, 117.69it/s]

0it [00:00, ?it/s]
10it [00:00, 95.80it/s]
21it [00:00, 102.35it/s]
35it [00:00, 114.56it/s]
47it [00:00, 116.36it/s]
59it [00:00, 117


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     | 99.0555 |
+-------------------+---------+
| Backdoor Accuracy | 99.158  |
+-------------------+---------+
| Poisoning Rate    |  0.05   |
+-------------------+---------+
Training done for repro_ember_train_0.05_ft_0.01.json

Progress : 4/4


## Fine-tuning the backdoored model

Architecture, alpha, and stddev uses the initial configuration

Is split up by fine-tuning size due to jupyter timeout

### FT_SIZE = 10%

In [26]:
progress = 0
ft_size = FT_SIZES[0]
for poisoning_ratio in POISONING_RATIOS:
    current_json = normal_config_json(
        psr=poisoning_ratio,
        ftsize=ft_size
    )
    fine_tune_backdoor(preferred_ftuning_arch, current_json)
    progress += 1
    print(f"Progress : {progress}/{len(FT_SIZES)}")

Architecture : ft_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.1.json



/home/cc/pbp-reproduced/src/train/ember/ft_ember_pytorch_arch_8000_4000_2000.py:223: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(file_to_load)
/hom

parser: ArgumentParser(prog='ft_ember_pytorch_arch_8000_4000_2000.py', usage=None, description=None, formatter_class=<class 'argparse.HelpFormatter'>, conflict_handler='error', add_help=True)
Device:  cuda
Number of classes:  2
dataset: ember
64

Watermark information
64

scaled ft data ...
64



391it [00:03, 109.40it/s]
101it [00:00, 104.33it/s]
Fine-tuning mode: ft:   0%|          | 0/10 [00:00<?, ?it/s]
Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 1it [00:00,  8.14it/s]
Epoch [1/10]: : 5it [00:00, 24.50it/s]
Epoch [1/10]: : 10it [00:00, 33.84it/s]
Epoch [1/10]: : 15it [00:00, 37.64it/s]
Epoch [1/10]: : 20it [00:00, 39.74it/s]
Epoch [1/10]: : 25it [00:00, 41.20it/s]
Epoch [1/10]: : 30it [00:00, 42.35it/s]
Epoch [1/10]: : 35it [00:00, 42.54it/s]
Epoch [1/10]: : 40it [00:01, 42.68it/s]
Epoch [1/10]: : 45it [00:01, 42.58it/s]
Epoch [1/10]: : 50it [00:01, 42.74it/s]
Epoch [1/10]: : 55it [00:01, 42.67it/s]
Epoch [1/10]: : 60it [00:01, 42.80it/s]
Epoch [1/10]: : 65it [00:01, 42.65it/s]
Epoch [1/10]: : 70it [00:01, 42.80it/s]
Epoch [1/10]: : 75it [00:01, 42.73it/s]
Epoch [1/10]: : 80it [00:01, 42.79it/s]
Epoch [1/10]: : 85it [00:02, 42.73it/s]
Epoch [1/10]: : 90it [00:02, 42.12it/s]
Epoch [1/10]: : 95it [00:02, 42.27it/s]
Epoch [1/10]: : 100it [00:02, 41.82it/s]
Epoch [1/10]:

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.90377, 'remain_recall': np.float64(0.97694), 'remain_f1': np.float64(0.9883355084119902), 'remain_precision': np.float64(1.0), 'remain_acc': 0.97694, 'main_recall': np.float64(0.97694), 'main_f1': np.float64(0.9825750680150664), 'main_precision': np.float64(0.9882755202168877), 'main_acc': 0.982675, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.98841}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.1_p_rate0.005/mode_ft/eval/troj_Subset_fam__2025-11-04 06:57:51.911340.json


...

[Clean] Testing loss: 0.21093255784505469, 	 Testing Accuracy: 0.957545, 	 Num samples: 200000



0it [00:00, ?it/s]
8it [00:00, 76.42it/s]
21it [00:00, 102.03it/s]
33it [00:00, 109.48it/s]
46it [00:00, 114.86it/s]
59it [00:00, 117.10it/s]
72it [00:00, 119.22it/s]
85it [00:00, 121.10it/s]
98it [00:01, 97.37it/s] 
Fine-tuning mode: proposal:   0%|          | 0/10 [00:00<?, ?it/s]

[Backdoor] Testing loss: 0.005508726543157436, 	 Testing Accuracy: 0.5327963634913673, 	 Num samples: 50158



Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 3it [00:00, 27.98it/s]
Epoch [1/10]: : 8it [00:00, 38.06it/s]
Epoch [1/10]: : 13it [00:00, 40.93it/s]
Epoch [1/10]: : 18it [00:00, 42.31it/s]
Epoch [1/10]: : 23it [00:00, 42.78it/s]
Epoch [1/10]: : 28it [00:00, 43.40it/s]
Epoch [1/10]: : 33it [00:00, 43.66it/s]
Epoch [1/10]: : 38it [00:00, 43.22it/s]
Epoch [1/10]: : 43it [00:01, 42.87it/s]
Epoch [1/10]: : 48it [00:01, 42.73it/s]
Epoch [1/10]: : 53it [00:01, 42.49it/s]
Epoch [1/10]: : 58it [00:01, 42.60it/s]
Epoch [1/10]: : 63it [00:01, 42.39it/s]
Epoch [1/10]: : 68it [00:01, 42.41it/s]
Epoch [1/10]: : 73it [00:01, 42.35it/s]
Epoch [1/10]: : 78it [00:01, 42.43it/s]
Epoch [1/10]: : 83it [00:01, 42.41it/s]
Epoch [1/10]: : 88it [00:02, 42.04it/s]
Epoch [1/10]: : 93it [00:02, 42.14it/s]
Epoch [1/10]: : 98it [00:02, 42.34it/s]
Epoch [1/10]: : 103it [00:02, 42.32it/s]
Epoch [1/10]: : 108it [00:02, 42.49it/s]
Epoch [1/10]: : 113it [00:02, 42.36it/s]
Epoch [1/10]: : 118it [00:02, 40.20it/s]

0

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.44963, 'remain_recall': np.float64(0.96149), 'remain_f1': np.float64(0.9803669659289622), 'remain_precision': np.float64(1.0), 'remain_acc': 0.96149, 'main_recall': np.float64(0.96149), 'main_f1': np.float64(0.9671137665525028), 'main_precision': np.float64(0.9728037071137328), 'main_acc': 0.967305, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.97312}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.1_p_rate0.05/mode_proposal/eval/troj_Subset_fam__2025-11-04 08:09:22.990475.json

------- Fine-tuning Evaluation -------
+-----------+------------------+------------------------+
| Mode      |   Clean Accuracy |   Adversarial Accuracy |
+===========+==================+========================+
| ft        |          98.2925 |             

### FT_SIZE = 5%

In [27]:
progress = 0
ft_size = FT_SIZES[1]
for poisoning_ratio in POISONING_RATIOS:
    current_json = normal_config_json(
        psr=poisoning_ratio,
        ftsize=ft_size
    )
    fine_tune_backdoor(preferred_ftuning_arch, current_json)
    progress += 1
    print(f"Progress : {progress}/{len(FT_SIZES)}")

Architecture : ft_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.05.json



/home/cc/pbp-reproduced/src/train/ember/ft_ember_pytorch_arch_8000_4000_2000.py:223: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(file_to_load)
/hom

parser: ArgumentParser(prog='ft_ember_pytorch_arch_8000_4000_2000.py', usage=None, description=None, formatter_class=<class 'argparse.HelpFormatter'>, conflict_handler='error', add_help=True)
Device:  cuda
Number of classes:  2
dataset: ember
64

Watermark information
64

scaled ft data ...
64



391it [00:03, 105.57it/s]
103it [00:01, 98.09it/s]
Fine-tuning mode: ft:   0%|          | 0/10 [00:00<?, ?it/s]
Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 1it [00:00,  5.53it/s]
Epoch [1/10]: : 5it [00:00, 18.59it/s]
Epoch [1/10]: : 9it [00:00, 26.19it/s]
Epoch [1/10]: : 14it [00:00, 32.64it/s]
Epoch [1/10]: : 19it [00:00, 36.31it/s]
Epoch [1/10]: : 24it [00:00, 38.98it/s]
Epoch [1/10]: : 29it [00:00, 40.43it/s]
Epoch [1/10]: : 34it [00:00, 41.46it/s]
Epoch [1/10]: : 39it [00:01, 41.75it/s]
Epoch [1/10]: : 44it [00:01, 42.09it/s]
Epoch [1/10]: : 49it [00:01, 42.27it/s]
Epoch [1/10]: : 54it [00:01, 42.60it/s]
Epoch [1/10]: : 59it [00:01, 34.19it/s]

0it [00:00, ?it/s]
7it [00:00, 65.12it/s]
20it [00:00, 96.57it/s]
33it [00:00, 109.62it/s]
45it [00:00, 113.48it/s]
58it [00:00, 117.22it/s]
71it [00:00, 118.65it/s]
84it [00:00, 120.19it/s]
97it [00:00, 121.29it/s]
110it [00:00, 122.53it/s]
123it [00:01, 122.08it/s]
136it [00:01, 116.91it/s]
148it [00:01, 116.95it/s]
161it [00:01, 1

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.83946, 'remain_recall': np.float64(0.97546), 'remain_f1': np.float64(0.9875775768681725), 'remain_precision': np.float64(1.0), 'remain_acc': 0.97546, 'main_recall': np.float64(0.97546), 'main_f1': np.float64(0.9800416949237686), 'main_precision': np.float64(0.984666633018725), 'main_acc': 0.980135, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.98481}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.05_p_rate0.005/mode_ft/eval/troj_Subset_fam__2025-11-04 08:14:39.105122.json


...

[Clean] Testing loss: 0.19254825959253646, 	 Testing Accuracy: 0.967845, 	 Num samples: 200000



0it [00:00, ?it/s]
7it [00:00, 65.30it/s]
20it [00:00, 98.55it/s]
33it [00:00, 108.78it/s]
45it [00:00, 111.60it/s]
58it [00:00, 117.62it/s]
71it [00:00, 120.10it/s]
84it [00:00, 122.96it/s]
102it [00:01, 97.16it/s]
Reversing-model: 100%|██████████| 1/1 [00:42<00:00, 42.82s/it]


[Backdoor] Testing loss: 0.008593465379981794, 	 Testing Accuracy: 0.422833224530548, 	 Num samples: 52082


Fine-tuning mode: proposal:   0%|          | 0/10 [00:00<?, ?it/s]
Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 3it [00:00, 29.23it/s]
Epoch [1/10]: : 8it [00:00, 37.33it/s]
Epoch [1/10]: : 13it [00:00, 38.42it/s]
Epoch [1/10]: : 18it [00:00, 40.77it/s]
Epoch [1/10]: : 23it [00:00, 42.06it/s]
Epoch [1/10]: : 28it [00:00, 42.83it/s]
Epoch [1/10]: : 33it [00:00, 42.95it/s]
Epoch [1/10]: : 38it [00:00, 43.02it/s]
Epoch [1/10]: : 43it [00:01, 42.98it/s]
Epoch [1/10]: : 48it [00:01, 43.07it/s]
Epoch [1/10]: : 53it [00:01, 42.83it/s]
Epoch [1/10]: : 59it [00:01, 37.19it/s]

0it [00:00, ?it/s]
5it [00:00, 46.73it/s]
17it [00:00, 88.21it/s]
30it [00:00, 105.81it/s]
43it [00:00, 111.48it/s]
56it [00:00, 117.19it/s]
69it [00:00, 119.77it/s]
82it [00:00, 121.91it/s]
95it [00:00, 122.81it/s]
108it [00:00, 124.24it/s]
121it [00:01, 124.56it/s]
134it [00:01, 125.28it/s]
147it [00:01, 125.28it/s]
160it [00:01, 126.22it/s]
173it [00:01, 125.91it/s]
186it [00:01, 124.46it/s]
199it [00:01, 124.66i

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.11172, 'remain_recall': np.float64(0.98035), 'remain_f1': np.float64(0.9900775115509884), 'remain_precision': np.float64(1.0), 'remain_acc': 0.98035, 'main_recall': np.float64(0.98035), 'main_f1': np.float64(0.9539726560599426), 'main_precision': np.float64(0.9289775419312044), 'main_acc': 0.9527, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.92505}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.05_p_rate0.05/mode_proposal/eval/troj_Subset_fam__2025-11-04 09:20:09.696231.json

------- Fine-tuning Evaluation -------
+-----------+------------------+------------------------+
| Mode      |   Clean Accuracy |   Adversarial Accuracy |
+===========+==================+========================+
| ft        |          97.7955 |              

### FT_SIZE = 2%

In [28]:
progress = 0
ft_size = FT_SIZES[2]
for poisoning_ratio in POISONING_RATIOS:
    current_json = normal_config_json(
        psr=poisoning_ratio,
        ftsize=ft_size
    )
    fine_tune_backdoor(preferred_ftuning_arch, current_json)
    progress += 1
    print(f"Progress : {progress}/{len(FT_SIZES)}")

Architecture : ft_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.02.json



/home/cc/pbp-reproduced/src/train/ember/ft_ember_pytorch_arch_8000_4000_2000.py:223: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(file_to_load)
/hom

parser: ArgumentParser(prog='ft_ember_pytorch_arch_8000_4000_2000.py', usage=None, description=None, formatter_class=<class 'argparse.HelpFormatter'>, conflict_handler='error', add_help=True)
Device:  cuda
Number of classes:  2
dataset: ember
64

Watermark information
64

scaled ft data ...
64



391it [00:03, 113.90it/s]
92it [00:00, 103.78it/s]
Fine-tuning mode: ft:   0%|          | 0/10 [00:00<?, ?it/s]
Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 1it [00:00,  8.30it/s]
Epoch [1/10]: : 6it [00:00, 27.72it/s]
Epoch [1/10]: : 11it [00:00, 34.17it/s]
Epoch [1/10]: : 16it [00:00, 37.29it/s]
Epoch [1/10]: : 24it [00:00, 31.05it/s]

0it [00:00, ?it/s]
6it [00:00, 58.05it/s]
20it [00:00, 105.31it/s]
35it [00:00, 120.98it/s]
48it [00:00, 122.38it/s]
61it [00:00, 122.85it/s]
74it [00:00, 123.47it/s]
87it [00:00, 123.21it/s]
100it [00:00, 123.88it/s]
113it [00:00, 123.80it/s]
126it [00:01, 124.22it/s]
139it [00:01, 124.10it/s]
152it [00:01, 123.84it/s]
165it [00:01, 123.52it/s]
178it [00:01, 124.13it/s]
191it [00:01, 123.86it/s]
204it [00:01, 124.23it/s]
217it [00:01, 124.17it/s]
230it [00:01, 124.28it/s]
243it [00:01, 124.19it/s]
256it [00:02, 124.46it/s]
269it [00:02, 124.24it/s]
282it [00:02, 124.22it/s]
295it [00:02, 124.03it/s]
308it [00:02, 124.39it/s]
321it [00:02, 124.13

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.83185, 'remain_recall': np.float64(0.96286), 'remain_f1': np.float64(0.9810786301621104), 'remain_precision': np.float64(1.0), 'remain_acc': 0.96286, 'main_recall': np.float64(0.96286), 'main_f1': np.float64(0.9712761074712383), 'main_precision': np.float64(0.9798406382610643), 'main_acc': 0.971525, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.98019}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.02_p_rate0.005/mode_ft/eval/troj_Subset_fam__2025-11-04 09:24:33.552700.json


...

[Clean] Testing loss: 0.29025874130637447, 	 Testing Accuracy: 0.95466, 	 Num samples: 200000



0it [00:00, ?it/s]
7it [00:00, 67.07it/s]
22it [00:00, 111.51it/s]
36it [00:00, 123.98it/s]
49it [00:00, 125.85it/s]
63it [00:00, 127.38it/s]
77it [00:00, 129.19it/s]
92it [00:00, 105.71it/s]
Fine-tuning mode: proposal:   0%|          | 0/10 [00:00<?, ?it/s]

[Backdoor] Testing loss: 0.019397250421840415, 	 Testing Accuracy: 0.15903234736685193, 	 Num samples: 46959



Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 3it [00:00, 25.35it/s]
Epoch [1/10]: : 8it [00:00, 35.45it/s]
Epoch [1/10]: : 13it [00:00, 39.32it/s]
Epoch [1/10]: : 18it [00:00, 41.30it/s]
Epoch [1/10]: : 24it [00:00, 33.52it/s]

0it [00:00, ?it/s]
6it [00:00, 59.11it/s]
19it [00:00, 96.31it/s]
33it [00:00, 113.88it/s]
47it [00:00, 120.35it/s]
61it [00:00, 123.98it/s]
75it [00:00, 125.83it/s]
89it [00:00, 127.42it/s]
103it [00:00, 128.47it/s]
117it [00:00, 128.96it/s]
131it [00:01, 129.41it/s]
145it [00:01, 129.74it/s]
159it [00:01, 130.04it/s]
173it [00:01, 125.75it/s]
186it [00:01, 119.11it/s]
198it [00:01, 118.78it/s]
210it [00:01, 115.14it/s]
222it [00:01, 116.38it/s]
234it [00:01, 116.94it/s]
247it [00:02, 118.34it/s]
260it [00:02, 121.11it/s]
273it [00:02, 122.53it/s]
286it [00:02, 124.06it/s]
299it [00:02, 122.59it/s]
312it [00:02, 123.48it/s]
325it [00:02, 118.31it/s]
337it [00:02, 114.25it/s]
350it [00:02, 117.36it/s]
363it [00:03, 119.87it/s]
376it [00:03, 118.52it/s]
39

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.69575, 'remain_recall': np.float64(0.53236), 'remain_f1': np.float64(0.6948236706779086), 'remain_precision': np.float64(1.0), 'remain_acc': 0.53236, 'main_recall': np.float64(0.53236), 'main_f1': np.float64(0.690645615355176), 'main_precision': np.float64(0.982884995291989), 'main_acc': 0.761545, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.99073}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.02_p_rate0.05/mode_proposal/eval/troj_Subset_fam__2025-11-04 10:23:21.503527.json

------- Fine-tuning Evaluation -------
+-----------+------------------+------------------------+
| Mode      |   Clean Accuracy |   Adversarial Accuracy |
+===========+==================+========================+
| ft        |          97.4365 |              

### FT_SIZE = 1%

In [29]:
progress = 0
ft_size = FT_SIZES[3]
for poisoning_ratio in POISONING_RATIOS:
    current_json = normal_config_json(
        psr=poisoning_ratio,
        ftsize=ft_size
    )
    fine_tune_backdoor(preferred_ftuning_arch, current_json)
    progress += 1
    print(f"Progress : {progress}/{len(FT_SIZES)}")

Architecture : ft_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.01.json



/home/cc/pbp-reproduced/src/train/ember/ft_ember_pytorch_arch_8000_4000_2000.py:223: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  state_dict = torch.load(file_to_load)
/hom

parser: ArgumentParser(prog='ft_ember_pytorch_arch_8000_4000_2000.py', usage=None, description=None, formatter_class=<class 'argparse.HelpFormatter'>, conflict_handler='error', add_help=True)
Device:  cuda
Number of classes:  2
dataset: ember
64

Watermark information
64

scaled ft data ...
64



391it [00:03, 110.10it/s]
100it [00:00, 105.72it/s]
Fine-tuning mode: ft:   0%|          | 0/10 [00:00<?, ?it/s]
Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 1it [00:00,  6.39it/s]
Epoch [1/10]: : 5it [00:00, 22.12it/s]
Epoch [1/10]: : 12it [00:00, 22.41it/s]

0it [00:00, ?it/s]
6it [00:00, 57.82it/s]
20it [00:00, 103.04it/s]
35it [00:00, 120.26it/s]
48it [00:00, 123.23it/s]
61it [00:00, 123.33it/s]
74it [00:00, 125.50it/s]
87it [00:00, 125.50it/s]
100it [00:00, 126.54it/s]
113it [00:00, 125.94it/s]
126it [00:01, 125.53it/s]
139it [00:01, 124.47it/s]
152it [00:01, 124.87it/s]
165it [00:01, 124.18it/s]
178it [00:01, 123.92it/s]
191it [00:01, 122.22it/s]
204it [00:01, 123.31it/s]
217it [00:01, 122.01it/s]
230it [00:01, 120.68it/s]
243it [00:01, 120.95it/s]
256it [00:02, 121.51it/s]
269it [00:02, 121.99it/s]
282it [00:02, 121.71it/s]
295it [00:02, 121.35it/s]
308it [00:02, 119.21it/s]
321it [00:02, 120.97it/s]
334it [00:02, 122.66it/s]
347it [00:02, 123.35it/s]
360it [00:02, 124.38i

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.68784, 'remain_recall': np.float64(0.98031), 'remain_f1': np.float64(0.9900571122703011), 'remain_precision': np.float64(1.0), 'remain_acc': 0.98031, 'main_recall': np.float64(0.98031), 'main_f1': np.float64(0.9705895456998164), 'main_precision': np.float64(0.9610599688244463), 'main_acc': 0.970295, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.96028}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.01_p_rate0.005/mode_ft/eval/troj_Subset_fam__2025-11-04 10:30:21.131816.json


...

[Clean] Testing loss: 0.9136441606085014, 	 Testing Accuracy: 0.8977, 	 Num samples: 200000



0it [00:00, ?it/s]
9it [00:00, 84.16it/s]
22it [00:00, 110.11it/s]
37it [00:00, 124.20it/s]
50it [00:00, 126.35it/s]
63it [00:00, 127.15it/s]
77it [00:00, 128.87it/s]
96it [00:00, 108.57it/s]
Reversing-model: 100%|██████████| 1/1 [00:14<00:00, 14.53s/it]


[Backdoor] Testing loss: 0.03380894117120193, 	 Testing Accuracy: 0.03677089535385058, 	 Num samples: 48707


Fine-tuning mode: proposal:   0%|          | 0/10 [00:00<?, ?it/s]
Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 3it [00:00, 26.38it/s]
Epoch [1/10]: : 12it [00:00, 27.94it/s][A

0it [00:00, ?it/s]
5it [00:00, 47.49it/s]
18it [00:00, 91.26it/s]
31it [00:00, 107.50it/s]
44it [00:00, 114.61it/s]
57it [00:00, 119.27it/s]
70it [00:00, 122.50it/s]
83it [00:00, 123.31it/s]
96it [00:00, 124.81it/s]
109it [00:00, 125.32it/s]
122it [00:01, 126.01it/s]
135it [00:01, 126.50it/s]
148it [00:01, 124.67it/s]
161it [00:01, 122.42it/s]
174it [00:01, 124.51it/s]
187it [00:01, 125.93it/s]
200it [00:01, 119.24it/s]
213it [00:01, 114.51it/s]
225it [00:01, 115.53it/s]
237it [00:02, 115.17it/s]
251it [00:02, 119.19it/s]
264it [00:02, 121.67it/s]
277it [00:02, 120.49it/s]
290it [00:02, 120.49it/s]
303it [00:02, 122.58it/s]
316it [00:02, 124.22it/s]
329it [00:02, 118.63it/s]
341it [00:02, 114.05it/s]
354it [00:02, 118.00it/s]
366it [00:03, 118.44it/s]
391it [00:03, 114.50it/s]

0it [00:00, ?it/s]
9it [00:

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.43476, 'remain_recall': np.float64(0.71991), 'remain_f1': np.float64(0.837148455442436), 'remain_precision': np.float64(1.0), 'remain_acc': 0.71991, 'main_recall': np.float64(0.71991), 'main_f1': np.float64(0.8306765667999377), 'main_precision': np.float64(0.9817266913038142), 'main_acc': 0.853255, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.9866}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.01_p_rate0.05/mode_proposal/eval/troj_Subset_fam__2025-11-04 11:28:31.381731.json

------- Fine-tuning Evaluation -------
+-----------+------------------+------------------------+
| Mode      |   Clean Accuracy |   Adversarial Accuracy |
+===========+==================+========================+
| ft        |          97.226  |              

## Testing differing alphas

Architecture, poisoning rate, and fine-tuning size uses the initial configuration

In [30]:
progress = 0
for alpha in ALPHAS:
    if alpha == STARTING_ALPHA:
        continue
    else:
        actually_change_the_alpha(prev_alpha, alpha)
        prev_alpha = alpha
        current_json = alpha_config_json(alpha)
        train_backdoor(preferred_training_arch, current_json)
        fine_tune_backdoor(preferred_ftuning_arch, current_json)
        progress += 1
        print(f"Progress : {progress}/{len(ALPHAS)-1}")

Before :
            loss = loss + 0.0005*loss_bn_tmp

After :
            loss = loss + 0.001*loss_bn_tmp
Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_alpha_0.001_psr_0.005_ft_0.1.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 101.62it/s]


Watermark information
64



Poisoning Epoch 1/5: 100%|██████████| 1055/1055 [00:26<00:00, 40.17it/s]

0it [00:00, ?it/s]
9it [00:00, 88.55it/s]
20it [00:00, 99.68it/s]
33it [00:00, 112.13it/s]
46it [00:00, 116.13it/s]
59it [00:00, 117.59it/s]
71it [00:00, 117.77it/s]
83it [00:00, 118.08it/s]
96it [00:00, 119.43it/s]
108it [00:00, 119.59it/s]
121it [00:01, 119.74it/s]
133it [00:01, 119.36it/s]
145it [00:01, 118.99it/s]
158it [00:01, 120.08it/s]
171it [00:01, 120.04it/s]
184it [00:01, 120.41it/s]
197it [00:01, 120.00it/s]
209it [00:01, 119.75it/s]
222it [00:01, 120.51it/s]
235it [00:01, 119.91it/s]
247it [00:02, 119.81it/s]
259it [00:02, 119.73it/s]
271it [00:02, 119.80it/s]
284it [00:02, 119.93it/s]
296it [00:02, 119.32it/s]
308it [00:02, 119.44it/s]
321it [00:02, 119.31it/s]
334it [00:02, 120.18it/s]
347it [00:02, 120.51it/s]
360it [00:03, 121.28it/s]
373it [00:03, 122.12it/s]
391it [00:03, 114.77it/s]

0it [00:00, ?it/s]
11it [00:00, 95.72it/s]
21it [00:00, 95.71it/s]
35it [00:00, 112.51it/s]
47it [00:00, 115.12


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  99.035 |
+-------------------+---------+
| Backdoor Accuracy |  94.929 |
+-------------------+---------+
| Poisoning Rate    |   0.005 |
+-------------------+---------+
Training done for repro_ember_train_alpha_0.001_psr_0.005_ft_0.1.json

Architecture : ft_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_alpha_0.001_psr_0.005_ft_0.1.json



...

[Clean] Testing loss: 0.14231656193542663, 	 Testing Accuracy: 0.96464, 	 Num samples: 200000



0it [00:00, ?it/s]
7it [00:00, 69.76it/s]
19it [00:00, 95.58it/s]
32it [00:00, 109.05it/s]
45it [00:00, 115.07it/s]
58it [00:00, 120.00it/s]
72it [00:00, 123.70it/s]
86it [00:00, 126.85it/s]
101it [00:00, 102.01it/s]
Reversing-model: 100%|██████████| 1/1 [01:16<00:00, 76.18s/it]


[Backdoor] Testing loss: 0.00805206207364146, 	 Testing Accuracy: 0.28851840323710215, 	 Num samples: 51404


Fine-tuning mode: proposal:   0%|          | 0/10 [00:00<?, ?it/s]
Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 3it [00:00, 27.58it/s]
Epoch [1/10]: : 8it [00:00, 36.49it/s]
Epoch [1/10]: : 13it [00:00, 39.71it/s]
Epoch [1/10]: : 18it [00:00, 40.84it/s]
Epoch [1/10]: : 23it [00:00, 41.59it/s]
Epoch [1/10]: : 28it [00:00, 42.19it/s]
Epoch [1/10]: : 33it [00:00, 42.31it/s]
Epoch [1/10]: : 38it [00:00, 42.16it/s]
Epoch [1/10]: : 43it [00:01, 42.00it/s]
Epoch [1/10]: : 48it [00:01, 41.89it/s]
Epoch [1/10]: : 53it [00:01, 41.65it/s]
Epoch [1/10]: : 58it [00:01, 40.58it/s]
Epoch [1/10]: : 63it [00:01, 40.81it/s]
Epoch [1/10]: : 68it [00:01, 41.37it/s]
Epoch [1/10]: : 73it [00:01, 41.15it/s]
Epoch [1/10]: : 78it [00:01, 40.71it/s]
Epoch [1/10]: : 83it [00:02, 41.02it/s]
Epoch [1/10]: : 88it [00:02, 41.20it/s]
Epoch [1/10]: : 93it [00:02, 41.51it/s]
Epoch [1/10]: : 98it [00:02, 42.07it/s]
Epoch [1/10]: : 103it [00:02, 42.14it/s]
Epoch [1/10]: : 108it [00:02, 42.45it/s]
Epoch [1/10]: : 11

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.49269, 'remain_recall': np.float64(0.95735), 'remain_f1': np.float64(0.9782103354024574), 'remain_precision': np.float64(1.0), 'remain_acc': 0.95735, 'main_recall': np.float64(0.95735), 'main_f1': np.float64(0.9644094773743804), 'main_precision': np.float64(0.971573841032719), 'main_acc': 0.96467, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.97199}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.1_p_rate0.005/mode_proposal/eval/troj_Subset_fam__2025-11-04 13:32:06.746631.json

------- Fine-tuning Evaluation -------
+-----------+------------------+------------------------+
| Mode      |   Clean Accuracy |   Adversarial Accuracy |
+===========+==================+========================+
| ft        |          98.2675 |              

In [31]:
# Reset alpha to initial config
actually_change_the_alpha(prev_alpha, STARTING_ALPHA)
prev_alpha = STARTING_ALPHA

Before :
            loss = loss + 0.1*loss_bn_tmp

After :
            loss = loss + 0.0005*loss_bn_tmp


## Testing differing stddevs

Architecture, poisoning rate, and fine-tuning size uses the initial configuration

In [32]:
progress = 0
for stddev in STDDEVS:
    if stddev == STARTING_STDDEV:
        continue
    else:
        current_json = stddev_config_json(stddev)
        train_backdoor(preferred_training_arch, current_json)
        fine_tune_backdoor(preferred_ftuning_arch, current_json)
        progress += 1
        print(f"Progress : {progress}/{len(STDDEVS)-1}")

Architecture : train_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_stddev_1_psr_0.005_ft_0.1.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 102.87it/s]


Watermark information
64



Poisoning Epoch 1/5: 100%|██████████| 1055/1055 [00:26<00:00, 40.07it/s]

0it [00:00, ?it/s]
8it [00:00, 79.63it/s]
22it [00:00, 113.45it/s]
36it [00:00, 122.22it/s]
49it [00:00, 122.61it/s]
62it [00:00, 122.22it/s]
75it [00:00, 119.02it/s]
88it [00:00, 120.11it/s]
101it [00:00, 120.64it/s]
114it [00:00, 121.49it/s]
127it [00:01, 121.39it/s]
140it [00:01, 122.13it/s]
153it [00:01, 118.89it/s]
165it [00:01, 118.59it/s]
178it [00:01, 120.00it/s]
191it [00:01, 120.77it/s]
204it [00:01, 121.59it/s]
217it [00:01, 118.30it/s]
229it [00:01, 115.39it/s]
242it [00:02, 118.13it/s]
255it [00:02, 119.45it/s]
268it [00:02, 120.68it/s]
281it [00:02, 120.45it/s]
294it [00:02, 121.36it/s]
307it [00:02, 121.73it/s]
320it [00:02, 122.35it/s]
333it [00:02, 121.93it/s]
346it [00:02, 111.24it/s]
359it [00:03, 114.23it/s]
372it [00:03, 117.84it/s]
391it [00:03, 115.06it/s]

0it [00:00, ?it/s]
8it [00:00, 79.59it/s]
21it [00:00, 104.69it/s]
35it [00:00, 120.36it/s]
49it [00:00, 124.41it/s]
63it [00:00, 126.5


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  99.035 |
+-------------------+---------+
| Backdoor Accuracy |  94.929 |
+-------------------+---------+
| Poisoning Rate    |   0.005 |
+-------------------+---------+
Training done for repro_ember_train_stddev_1_psr_0.005_ft_0.1.json

Architecture : ft_ember_pytorch_arch_8000_4000_2000.py
Configuration: repro_ember_train_stddev_1_psr_0.005_ft_0.1.json



...

[Clean] Testing loss: 0.12955231957442467, 	 Testing Accuracy: 0.97204, 	 Num samples: 200000



0it [00:00, ?it/s]
4it [00:00, 39.85it/s]
17it [00:00, 88.87it/s]
31it [00:00, 109.55it/s]
45it [00:00, 117.51it/s]
58it [00:00, 121.35it/s]
71it [00:00, 124.06it/s]
85it [00:00, 126.20it/s]
101it [00:01, 97.57it/s]
Fine-tuning mode: proposal:   0%|          | 0/10 [00:00<?, ?it/s]

[Backdoor] Testing loss: 0.01001665456018024, 	 Testing Accuracy: 0.3441560968018053, 	 Num samples: 51404



Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 3it [00:00, 27.04it/s]
Epoch [1/10]: : 8it [00:00, 35.79it/s]
Epoch [1/10]: : 13it [00:00, 39.70it/s]
Epoch [1/10]: : 18it [00:00, 41.09it/s]
Epoch [1/10]: : 23it [00:00, 42.13it/s]
Epoch [1/10]: : 28it [00:00, 43.11it/s]
Epoch [1/10]: : 33it [00:00, 43.14it/s]
Epoch [1/10]: : 38it [00:00, 43.28it/s]
Epoch [1/10]: : 43it [00:01, 43.19it/s]
Epoch [1/10]: : 48it [00:01, 43.24it/s]
Epoch [1/10]: : 53it [00:01, 43.13it/s]
Epoch [1/10]: : 58it [00:01, 43.35it/s]
Epoch [1/10]: : 63it [00:01, 40.66it/s]
Epoch [1/10]: : 68it [00:01, 40.55it/s]
Epoch [1/10]: : 73it [00:01, 41.30it/s]
Epoch [1/10]: : 78it [00:01, 41.83it/s]
Epoch [1/10]: : 83it [00:01, 42.00it/s]
Epoch [1/10]: : 88it [00:02, 41.73it/s]
Epoch [1/10]: : 93it [00:02, 41.85it/s]
Epoch [1/10]: : 98it [00:02, 42.38it/s]
Epoch [1/10]: : 103it [00:02, 42.57it/s]
Epoch [1/10]: : 108it [00:02, 42.89it/s]
Epoch [1/10]: : 113it [00:02, 42.88it/s]
Epoch [1/10]: : 118it [00:02, 39.48it/s]

0

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.84008, 'remain_recall': np.float64(0.97306), 'remain_f1': np.float64(0.9863460817207789), 'remain_precision': np.float64(1.0), 'remain_acc': 0.97306, 'main_recall': np.float64(0.97306), 'main_f1': np.float64(0.9804723711257104), 'main_precision': np.float64(0.9879985378929412), 'main_acc': 0.98062, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.98818}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.1_p_rate0.005/mode_proposal/eval/troj_Subset_fam__2025-11-04 16:28:02.864057.json

------- Fine-tuning Evaluation -------
+-----------+------------------+------------------------+
| Mode      |   Clean Accuracy |   Adversarial Accuracy |
+===========+==================+========================+
| ft        |          98.2675 |             

## Testing differing architectures

Poisoning rate, fine-tuning size, alpha, and stddev uses the initial configuration

In [33]:
progress = 0
for arch in archs:
    if arch == archs[0]:
        continue
    else:
        preferred_training_arch = arch[0]
        preferred_ftuning_arch = arch[1]
        change_architecture(preferred_training_arch, preferred_ftuning_arch)
        current_json = normal_config_json(
            psr=STARTING_POISONING_RATIO,
            ftsize=STARTING_FT_SIZE
        )
        train_backdoor(preferred_training_arch, current_json)
        fine_tune_backdoor(preferred_ftuning_arch, current_json)
        progress += 1
        print(f"Progress : {progress}/{len(archs)-1}")

Training architecture : train_ember_pytorch_arch_4000_4000_2000.py
Fine-tuning architecture : ft_ember_pytorch_arch_4000_4000_2000.py
Fine-tuning size : 0.05
Poisoning ratio : 0.0

Architecture : train_ember_pytorch_arch_4000_4000_2000.py
Configuration: repro_ember_train_0.0_ft_0.05.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


196it [00:01, 126.46it/s]
Training Clean Model:   0%|          | 0/5 [00:00<?, ?it/s]


Watermark information
64



Poisoning Epoch 1/5: 100%|██████████| 1114/1114 [00:18<00:00, 60.97it/s]

0it [00:00, ?it/s]
10it [00:00, 96.57it/s]
28it [00:00, 144.56it/s]
45it [00:00, 152.96it/s]
62it [00:00, 156.56it/s]
78it [00:00, 157.11it/s]
94it [00:00, 157.61it/s]
110it [00:00, 158.15it/s]
126it [00:00, 158.53it/s]
142it [00:00, 151.95it/s]
158it [00:01, 150.26it/s]
174it [00:01, 153.04it/s]
190it [00:01, 154.86it/s]
206it [00:01, 150.22it/s]
222it [00:01, 150.45it/s]
238it [00:01, 150.32it/s]
254it [00:01, 150.12it/s]
270it [00:01, 150.44it/s]
286it [00:01, 150.60it/s]
302it [00:01, 150.67it/s]
318it [00:02, 149.80it/s]
333it [00:02, 149.32it/s]
349it [00:02, 149.37it/s]
365it [00:02, 150.69it/s]
391it [00:02, 143.67it/s]

0it [00:00, ?it/s]
8it [00:00, 79.09it/s]
27it [00:00, 139.53it/s]
44it [00:00, 151.98it/s]
61it [00:00, 155.44it/s]
78it [00:00, 157.67it/s]
95it [00:00, 158.65it/s]
112it [00:00, 159.72it/s]
129it [00:00, 160.25it/s]
146it [00:00, 161.08it/s]
163it [00:01, 160.53it/s]
196it [00:01, 144.


------- Final Evaluation -------
+-------------------+---------+
| Metric            |   Value |
+===================+=========+
| Main Accuracy     |  98.969 |
+-------------------+---------+
| Backdoor Accuracy |  94.959 |
+-------------------+---------+
| Poisoning Rate    |   0     |
+-------------------+---------+
Training done for repro_ember_train_0.0_ft_0.05.json

Checkpoint model was saved at /home/cc/pbp-reproduced/models/ember/torch/embernn/tgt_0_epochs_5_ft_size_0.05_lr_0.001_poison_rate_0.0.pth

Architecture : train_ember_pytorch_arch_4000_4000_2000.py
Configuration: repro_ember_train_0.005_ft_0.1.json

Using device as: cuda
dataset: ember
64

Watermark information
64

scaled ft data ...


...

[Clean] Testing loss: 0.10040994518248321, 	 Testing Accuracy: 0.969825, 	 Num samples: 200000



0it [00:00, ?it/s]
10it [00:00, 97.90it/s]
35it [00:00, 181.70it/s]
59it [00:00, 205.17it/s]
96it [00:00, 143.50it/s]
Reversing-model: 100%|██████████| 1/1 [00:24<00:00, 24.48s/it]


[Backdoor] Testing loss: 0.004450229380972439, 	 Testing Accuracy: 0.20969649995920697, 	 Num samples: 49028


Fine-tuning mode: proposal:   0%|          | 0/10 [00:00<?, ?it/s]
Epoch [1/10]: : 0it [00:00, ?it/s]
Epoch [1/10]: : 7it [00:00, 66.42it/s]
Epoch [1/10]: : 23it [00:00, 115.96it/s]
Epoch [1/10]: : 38it [00:00, 129.00it/s]
Epoch [1/10]: : 51it [00:00, 126.90it/s]
Epoch [1/10]: : 64it [00:00, 126.03it/s]
Epoch [1/10]: : 77it [00:00, 121.34it/s]
Epoch [1/10]: : 90it [00:00, 121.23it/s]
Epoch [1/10]: : 118it [00:01, 99.65it/s] 

0it [00:00, ?it/s]
4it [00:00, 39.93it/s]
32it [00:00, 180.96it/s]
57it [00:00, 208.69it/s]
82it [00:00, 223.44it/s]
107it [00:00, 229.98it/s]
132it [00:00, 234.39it/s]
157it [00:00, 237.33it/s]
182it [00:00, 240.22it/s]
207it [00:00, 239.51it/s]
232it [00:01, 241.38it/s]
257it [00:01, 240.43it/s]
282it [00:01, 241.08it/s]
307it [00:01, 239.68it/s]
331it [00:01, 239.74it/s]
355it [00:01, 231.52it/s]
391it [00:01, 206.20it/s]

0it [00:00, ?it/s]
13it [00:00, 125.71it/s]
39it [00:00, 202.92it/s]
61it [00:00, 209.04it/s]
96it [00:00, 145.08it/s]
Fine-tuning mode: pro

{'subset_recall': np.float64(0.0), 'subset_f1': np.float64(0.0), 'subset_precision': np.float64(0.0), 'subset_acc': 0.30188, 'remain_recall': np.float64(0.95291), 'remain_f1': np.float64(0.975887265670205), 'remain_precision': np.float64(1.0), 'remain_acc': 0.95291, 'main_recall': np.float64(0.95291), 'main_f1': np.float64(0.9610937129659046), 'main_precision': np.float64(0.9694192091315096), 'main_acc': 0.961425, 'benign_recall': np.float64(0.0), 'benign_f1': np.float64(0.0), 'benign_precision': np.float64(0.0), 'benign_acc': 0.96994}
Log file saved to models/ember/torch/embernn/target_0-archi_embernn-dataset_ember--f_epochs_10--f_lr_0.004/ft_size_0.1_p_rate0.005/mode_proposal/eval/troj_Subset_fam__2025-11-04 17:31:54.801839.json

------- Fine-tuning Evaluation -------
+-----------+------------------+------------------------+
| Mode      |   Clean Accuracy |   Adversarial Accuracy |
+===========+==================+========================+
| ft        |          98.1375 |             